# cronIP.py - Versión 1.0.0.
En esta versión se envian algunos más datos por email, como la temperatura a la que se encuentra la CPU y la GPU del dispositivo Raspberry PI.
También esta diseñado para ser llamado solo una vez, y el proprio programa enviar un email cada 60 segundos.

En futuras versiones el objetivo es que se envíe un solo email en la primera conexión y que el resto de mensajes se guarden en una base de datos dentro de un servidor. También será interesante conocer más datos del dispositivo, así como la MAC y datos más relevantes que permitan identificar dónde y quien ejecuta el dispositivo. Y en caso de ser una conexión no permitida, poder para o inutilizarlo a distancia.

In [ ]:
#!/usr/bin/python
# -*- coding: utf-8 -*-

#########################################################################################################
 #    2018/02/17    Python 3    Versión 1.0.0. cronIP.py
 #
 #        Envía un email informando del tipo de dispositivo, la ip y el momento en el cual establece
 #        conexión. Cada minuto envía un email con información relativa a temperaturas y tiempo de conexión.
 #   
 #    2017/12/30    Python 3    Versión 0.3    cronIP.py
 #    2017/10/28    Python 3    Versión 0.2    ip_mail.py
 # 
 #    Autor:        Juan de Dios Yáñez Ávila
 #    Contacto:     juandediosyanez@onw4rds.com
 #    Empresa:      Onwards
 #    Dirección:    www.onw4rds.com                                                                                                      
 #                                                                                                       
 #    Este programa se ejecuta gracias a crontab justo en el momento que el dispositivo es conectado y
 #    durante cada minuto desde ese mismo momento.           
 #                                                                  
 #    Conecta con una cuenta de correo electrónico de Gmail para informar sobre la IP de conexión.                                                                                         
#########################################################################################################


import smtplib, socket, commands, os
import datetime
import ftplib
import time
from email.mime.text import MIMEText
from io import open

# Tenemos que dar un tiempo al sistema para que se establezca conexión a red y no de error.
# Ya que necesitamos conocer la IP de conexión y si no tenemos conexión a internet tampoco
# iniciará el programa.
time.sleep(30)

#############
# Obtención de datos
eConexion = datetime.datetime.now()       # fecha de establecimiento de conexión
dispositivo = socket.gethostbyname()      # nombre del dispositivo
ip = commands.getoutput('hostname -I')    # IP del dispositivo
tTranscurrido = 0                         # tiempo transcurrido de conexión

#########
# Conocer temperatura de la CPU y la GPU
def get_cpu_temp():
    tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
    cpu_temp = tempFile.read()
    tempFile.close()
    cpu_temp = str(float(cpu_temp)/1000) +"ºC"
    return cpu_temp
    #Mostrar temperatura en grados Fahrenheit
    #return float(1.8*cpu_temp)+32

def get_gpu_temp():
    gpu_temp = commands.getoutput( "/opt/vc/bin/vcgencmd measure_temp" ).replace( 'temp=', '' ).replace( 'C', '' )
    gpu_temp = str(float(gpu_temp)) + "ºC"
    return gpu_temp
    #Mostrar temperatura en grados Fahrenheit
    # return float(1.8* gpu_temp)+32

########
# Enviar email con la información de la IP y de que todo marcha como debe
def email_ip():
    global eConexion
    global dispositivo
    global ip
    global iConexion
    global tTranscurrido

    direccion_ip = str(dispositivo) + " | " + str(ip)
    cpu_temp = get_cpu_temp()
    gpu_temp = get_gpu_temp()
    
    #SCRIPT PARA CREAR EL MENSAJE
    mensaje = MIMEText("""
                       Dispositivo:  {0}
                       IP:    {1}
                       Conexión establecida a las:  {2}
                       Temperatura de la CPU: {3}
                       Temperatura de la GPU: {4}
                       
                       Tiempo de funcionamiento aproximado: {5} segundos""" .format(dispositivo, ip, eConexion, cpu_temp, gpu_temp, tTranscurrido))
    mensaje['From'] = "onw4rds@gmail.com"
    mensaje['To'] = "onw4rds@gmail.com"
    mensaje['Subject'] = direccion_ip

    #SCRIPT PARA EL ENVIO DEL CORREO ELECTRONICO
    mailServer = smtplib.SMTP('smtp.gmail.com', 587)
    mailServer.ehlo()
    mailServer.starttls()
    mailServer.ehlo()
    mailServer.login("onw4rds@gmail.com", "#GOovh47536485q??")
    mailServer.sendmail("onw4rds@gmail.com", "onw4rds@gmail.com", mensaje.as_string())
    ## def sendmail(from_addr, to_addrs, msg, mail_options=[], rcpt_options=[])
    mailServer.quit()

while True:
    email_ip()
    time.sleep(60)
    tTranscurrido = tTranscurrido + 60
